# Metropolis-Hastings MCMC
(on finite state spaces $\mathcal{X}$)

## Setup
Let $\mathcal{X} := \{-1, +1\}^d$, and $\mathbf{x} \in \mathcal{X}$. We define an *energy*
$$E(\mathbf{x}) = -\sum_{i=1}^d x_i x_{i+1}$$
with *periodic boundary conditions* $x_{d+1} := x_1$.

Target distribution:

$$\pi(\mathbf{x}) \propto \exp(-\beta E(\mathbf{x})) =: \tilde{\pi}(\mathbf{x})$$
where $\beta \geq 0$ is an inverse temperature parameter.

**Note**: $|\mathcal{X}| = 2^d$. For $d=64$, that's $18446744073709551616$ choices for $\mathbf{x}$.

In [1]:
import numpy as np

def log_pi_tilde(x: np.ndarray, beta: float = 1.0) -> float:
    """
    Computes log(tilde{\pi}(x)), i.e., the unnormalized log probability for x.

    Parameters
    ----------
    x : np.ndarray
        A 1D numpy array of length d with entries in {-1, +1}.
    beta : float, optional
        Inverse temperature parameter (default is 1.0).

    Returns
    -------
    float
        The unnormalized log probability of the configuration x.
    """

    energy = -np.sum(x * np.roll(x, -1))
    return -beta * energy

+ Initial distribution $p_1 := \text{Uniform}(\{-1, +1\}^d)$
+ Proposal $q(\hat{X}_{t+1} \mid X_{t} = \mathbf{x})$ is the uniform distribution over the $d$ strings that differ from $\mathbf{x}$ in exactly one bit
    + i.e., the proposal will flip a random bit
+ Note that the proposal is *symmetric*: $$q(\mathbf{y} \mid \mathbf{x}) = q(\mathbf{x} \mid \mathbf{y}) \quad \forall \mathbf{x}, \mathbf{y}$$
+ Thus, $$\alpha(\mathbf{x} \to \mathbf{y}) = \text{min}\left( 1, \ \frac{q(\mathbf{y} \mid \mathbf{x}) \tilde{\pi}(\mathbf{y})}{q(\mathbf{x} \mid \mathbf{y}) \tilde{\pi}(\mathbf{x})} \right) = \text{min}\left( 1, \ \frac{\tilde{\pi}(\mathbf{y})}{\tilde{\pi}(\mathbf{x})} \right)$$

In [6]:
def mh_random_flips(num_steps: int = 10_000, 
                    d: int = 64, 
                    beta: float = 0.7, 
                    seed: int = 0):
    rng = np.random.default_rng(seed)

    # Initialize x uniformly randomly \in {-1, +1}^d
    x = rng.choice([-1, 1], size=d)
    log_pi_tilde_x = log_pi_tilde(x, beta=beta)

    samples = np.zeros((num_steps, d), dtype=int)
    for t in range(num_steps):
        # 1) Propose: flip one random bit
        idx = rng.integers(d)
        x_prop = x.copy()
        x_prop[idx] *= -1  # flip one "bit"

        # 2) Compute acceptance probability alpha
        log_pi_tilde_prop = log_pi_tilde(x_prop, beta=beta)
        # Symmetric proposal => MH ratio uses only pi
        alpha = min(1, np.exp(log_pi_tilde_prop - log_pi_tilde_x))

        # 3) Accept/reject proposal
        U = rng.random()
        if U <= alpha:
            x = x_prop
            log_pi_tilde_x = log_pi_tilde_prop

        samples[t] = x

    return samples

*Let's draw samples!*

In [7]:
d = 64
beta = 0.7
samples = mh_random_flips(num_steps=1000, d=d, beta=beta, seed=123)

Visualizing the samples from $t=1$ to $t=1000$:

In [8]:
max_len = 1000

In [9]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import numpy as np

# Values in samples: -1 (dark), +1 (light)
samples_small = samples[:max_len]

fig, ax = plt.subplots(figsize=(12, 3.8))  # less tall
rects = []
pad_x = 0.05
pad_y = 0.18  # more space above/below, so rectangles less tall
spacing_x = (1 - 2 * pad_x) / samples_small.shape[1]
rect_height = 1 - 2 * pad_y
for i in range(samples_small.shape[1]):
    rect = plt.Rectangle((pad_x + i * spacing_x, pad_y), spacing_x * 0.95, rect_height, color='black')
    ax.add_patch(rect)
    rects.append(rect)

ax.set_xlim(0, 1)
ax.set_ylim(0, 1)
ax.axis('off')
fig.subplots_adjust(top=0.87)  # Make more room for the title

def update(frame):
    x = samples_small[frame]
    # Color: -1->dark (#222), +1->light (#eeeeee)
    for i, bit in enumerate(x):
        color = '#222222' if bit == -1 else '#eeeeee'
        rects[i].set_facecolor(color)
    ax.set_title(f"Step {frame+1}", fontsize=10, pad=10)  # Larger font and lower down
    return rects

anim = animation.FuncAnimation(fig, update, frames=len(samples_small), interval=30, blit=False)
plt.close(fig)

# To display animation in Jupyter:
from IPython.display import HTML
HTML(anim.to_jshtml())